<a href="https://colab.research.google.com/github/DEP04929/ESICMDatathon2026/blob/main/ExploringData_20260112.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Pre-requisites for Amsterdam UMC DB


In [2]:
# sets *your* project id
PROJECT_ID = "esicmdatathon2026" #@param {type:"string"}


In [3]:
# sets default dataset for AmsterdamUMCdb
DATASET_PROJECT_ID = 'amsterdamumcdb' #@param {type:"string"}
DATASET_ID = 'van_gogh_2026_datathon' #@param {type:"string"}
LOCATION = 'eu' #@param {type:"string"}

In [4]:
import os
from google.colab import auth

# all libraries check this environment variable, so set it:
os.environ["GOOGLE_CLOUD_PROJECT"] = PROJECT_ID

auth.authenticate_user()
print('Authenticated')


Authenticated


In [5]:
%load_ext google.colab.data_table
from google.colab.data_table import DataTable

# change default limits:
DataTable.max_columns = 50
DataTable.max_rows = 30000


In [6]:
from google.cloud.bigquery import magics
from google.cloud import bigquery

# sets the default query job configuration
def_config = bigquery.job.QueryJobConfig(default_dataset=DATASET_PROJECT_ID + "." + DATASET_ID)
magics.context.default_query_job_config = def_config


In [7]:
import pandas as pd
import numpy as np

import matplotlib as plt
import seaborn as sns
sns.set_style('darkgrid')

# Exploring data
Am trying to follow :
https://github.com/AmsterdamUMC/AmsterdamUMCdb/blob/master/omop/sql/ddl/bigquery.sql

Ventilator modes appear to be missing. Not possible to find specifics like HFOV for example.

In [ ]:
%%bigquery test --project esicmdatathon2026
select person_id, measurement_datetime, value_as_string, measurement_source_value
from measurement
where measurement_concept_id in (3004921 -- Ventilation mode Ventilator
)
--  and person_id = 51316 -- testing purpose only

Executing query with job ID: f3edb2a3-5700-41f1-8256-1d06e6ec0714
Query executing: 0.43s


ERROR:
 400 Unrecognized name: value_as_string at [1:41]; reason: invalidQuery, location: query, message: Unrecognized name: value_as_string at [1:41]

Location: EU
Job ID: f3edb2a3-5700-41f1-8256-1d06e6ec0714



In [ ]:
test


person_id      measurement_datetime  value_as_number  \
0        21307 2009-12-31 21:15:00+00:00              NaN   
1        21307 2009-12-31 21:09:00+00:00              NaN   
2        21307 2009-12-31 21:07:00+00:00              NaN   
3        21307 2009-12-31 20:58:00+00:00              NaN   
4        21307 2009-12-31 21:12:00+00:00              NaN   
..         ...                       ...              ...   
678      27693 2019-10-30 18:42:00+00:00              NaN   
679      10153 2020-02-03 15:23:00+00:00              NaN   
680      26860 2022-01-26 16:23:00+00:00              NaN   
681      26860 2022-02-01 03:23:00+00:00              NaN   
682       8316 2022-07-06 20:30:00+00:00              NaN   

                              measurement_source_value  
0            Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
1            Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
2            Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
3            Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
4            Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
..                                                 ...  
678             Beademingsmodus;R UMCA BEADEMINGSMODUS  
679             Beademingsmodus;R UMCA BEADEMINGSMODUS  
680  Modus Hamilton;R UMCA ICU VENTILATOR MODUS HAM...  
681             Beademingsmodus;R UMCA BEADEMINGSMODUS  
682             Beademingsmodus;R UMCA BEADEMINGSMODUS  

[683 rows x 4 columns]

Diagnosis is now condition, and without concepts. Just text based searching.

In [ ]:
%%bigquery test --project esicmdatathon2026
select *
from condition_occurrence
where person_id = 51316 -- 43138

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test


person_id  condition_concept_id condition_start_date  \
0      51316                     0           2017-01-01   
1      51316                     0           2017-01-01   
2      51316                     0           2017-01-23   

   condition_start_datetime condition_end_date condition_end_datetime  \
0 2017-01-01 02:00:00+00:00                NaT                    NaT   
1 2017-01-01 02:00:00+00:00                NaT                    NaT   
2 2017-01-23 16:15:00+00:00                NaT                    NaT   

   condition_type_concept_id  \
0                      32879   
1                      32879   
2                      32879   

                              condition_source_value  
0  Subarachnoid hemorrhage/intracranial aneurysm,...  
1  Coma/change in level of consciousness (for hep...  
2      Subarachnoid hemorrhage/intracranial aneurysm

It is possible to see modes of non-invasive ventilation

In [ ]:
%%bigquery test --project esicmdatathon2026
select * --person_id, measurement_date, measurement_datetime, value_as_number, value_source_value, measurement_source_value
from measurement
where measurement_concept_id in (2000000250 -- Ventilation mode Ventilator non-invasive
)
  and person_id = 49440 -- testing purpose only
limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test

person_id  measurement_concept_id measurement_date  \
0       49440              2000000250       2002-01-22   
1       49440              2000000250       2002-01-23   
2       49440              2000000250       2002-01-23   
3       49440              2000000250       2002-01-23   
4       49440              2000000250       2002-01-23   
5       49440              2000000250       2002-01-22   
6       49440              2000000250       2002-01-23   
7       49440              2000000250       2002-01-23   
8       49440              2000000250       2002-01-22   
9       49440              2000000250       2002-01-22   
10      49440              2000000250       2002-01-23   
11      49440              2000000250       2002-01-22   
12      49440              2000000250       2002-01-22   

        measurement_datetime  measurement_type_concept_id  value_as_number  \
0  2002-01-22 21:11:00+00:00                            0              5.0   
1  2002-01-23 10:11:00+00:00                            0              5.0   
2  2002-01-23 09:11:00+00:00                            0              5.0   
3  2002-01-23 13:11:00+00:00                            0              5.0   
4  2002-01-23 12:11:00+00:00                            0              5.0   
5  2002-01-22 23:11:00+00:00                            0              5.0   
6  2002-01-23 05:11:00+00:00                            0              5.0   
7  2002-01-23 01:11:00+00:00                            0              5.0   
8  2002-01-22 19:11:00+00:00                            0              5.0   
9  2002-01-22 20:11:00+00:00                            0              5.0   
10 2002-01-23 11:11:00+00:00                            0              5.0   
11 2002-01-22 18:11:00+00:00                            0              8.0   
12 2002-01-22 17:11:00+00:00                            0              8.0   

   measurement_source_value unit_source_value value_source_value  
0       CPAP (Bipap Vision)             cmH2O                5.0  
1       CPAP (Bipap Vision)             cmH2O                5.0  
2       CPAP (Bipap Vision)             cmH2O                5.0  
3       CPAP (Bipap Vision)             cmH2O                5.0  
4       CPAP (Bipap Vision)             cmH2O                5.0  
5       CPAP (Bipap Vision)             cmH2O                5.0  
6       CPAP (Bipap Vision)             cmH2O                5.0  
7       CPAP (Bipap Vision)             cmH2O                5.0  
8       CPAP (Bipap Vision)             cmH2O                5.0  
9       CPAP (Bipap Vision)             cmH2O                5.0  
10      CPAP (Bipap Vision)             cmH2O                5.0  
11      CPAP (Bipap Vision)             cmH2O                8.0  
12      CPAP (Bipap Vision)             cmH2O                8.0

In [ ]:
%%bigquery test --project esicmdatathon2026
select person_id, measurement_date, measurement_datetime, value_as_number, value_source_value, measurement_source_value, unit_source_value
from measurement
where measurement_concept_id in (-- 3043148 --Breath rate mechanical
                                 -- 1175625 -- Breath rate spontaneous
                                 -- 3026892 -- Breath rate spontaneous --on ventilator
                                 3024171 -- Respiratory rate
)
  and value_as_number is not null and value_as_number > 0
--  and person_id = 49440 -- testing purpose only
limit 100


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test


person_id measurement_date      measurement_datetime  value_as_number  \
0       17539       2009-08-29 2009-08-29 16:05:00+00:00              1.0   
1       17673       2009-12-29 2009-12-29 18:51:00+00:00              1.0   
2       18103       2009-12-31 2009-12-31 18:18:00+00:00              1.0   
3       17509       2009-12-31 2009-12-31 18:26:00+00:00              1.0   
4       17509       2009-12-31 2009-12-31 18:27:00+00:00              1.0   
..        ...              ...                       ...              ...   
95      16631       2016-12-31 2016-12-31 14:00:00+00:00              1.0   
96      16631       2016-12-31 2016-12-31 14:03:00+00:00              1.0   
97      17134       2016-12-31 2016-12-31 14:47:00+00:00              1.0   
98      17134       2016-12-31 2016-12-31 14:52:00+00:00              1.0   
99      17331       2016-12-31 2016-12-31 14:54:00+00:00              1.0   

   value_source_value       measurement_source_value unit_source_value  
0                 1.0   Respiratory Rate;R RESP RATE                    
1                 1.0   Respiratory Rate;R RESP RATE                    
2                 1.0  AF totaal;R UMCA AN AF TOTAAL                    
3                 1.0   Respiratory Rate;R RESP RATE                    
4                 1.0  AF totaal;R UMCA AN AF TOTAAL                    
..                ...                            ...               ...  
95                1.0   Respiratory Rate;R RESP RATE                    
96                1.0  AF totaal;R UMCA AN AF TOTAAL                    
97                1.0   Respiratory Rate;R RESP RATE                    
98                1.0   Respiratory Rate;R RESP RATE                    
99                1.0  AF totaal;R UMCA AN AF TOTAAL                    

[100 rows x 7 columns]

Quantity is there, but dose is not there, for drug exposure. I am unsure mg/ 24 hours unit meaning?  

In [ ]:
%%bigquery test --project esicmdatathon2026
select * --person_id, drug_exposure_start_datetime, drug_exposure_end_datetime, drug_concept_id, quantity
from drug_exposure
where drug_concept_id in (1736887 -- linezolid
                      ,1709170    -- Meropenem
                      ,1707687    -- vancomycin
                      ,1742253    -- Levofloxacin
                      ,1778162    -- Cefuroxim
                      ,1707164    -- Metronidazol
                      ,1777806    -- Ceftriaxone
                      ,1718054    -- Caspofungin
                      ,1754994    -- Fluconazole
                      ,997881     -- Clindamycin
                      )
      and person_id = 56647 -- testing only
  limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test

person_id  drug_concept_id drug_exposure_start_date  \
0       56647          1777806               2016-12-30   
1       56647          1742253               2017-01-08   
2       56647          1742253               2017-01-09   
3       56647          1742253               2017-01-09   
4       56647          1742253               2017-01-10   
..        ...              ...                      ...   
72      56647          1707687               2017-01-10   
73      56647          1709170               2017-01-11   
74      56647          1707687               2017-01-11   
75      56647          1707687               2017-01-28   
76      56647          1707687               2017-01-29   

   drug_exposure_start_datetime drug_exposure_end_date  \
0     2016-12-30 20:25:00+00:00             2016-12-30   
1     2017-01-08 14:34:00+00:00             2017-01-08   
2     2017-01-09 00:07:00+00:00             2017-01-09   
3     2017-01-09 11:55:00+00:00             2017-01-09   
4     2017-01-10 00:54:00+00:00             2017-01-10   
..                          ...                    ...   
72    2017-01-10 22:02:00+00:00             2017-01-10   
73    2017-01-11 10:07:00+00:00             2017-01-11   
74    2017-01-11 04:33:00+00:00             2017-01-11   
75    2017-01-28 05:21:00+00:00             2017-01-28   
76    2017-01-29 22:55:00+00:00             2017-01-29   

   drug_exposure_end_datetime  drug_type_concept_id  quantity  \
0   2016-12-30 20:25:00+00:00              38000180    2000.0   
1   2017-01-08 14:34:00+00:00              38000180     500.0   
2   2017-01-09 00:07:00+00:00              38000180     125.0   
3   2017-01-09 11:55:00+00:00              38000180     125.0   
4   2017-01-10 00:54:00+00:00              38000180     500.0   
..                        ...                   ...       ...   
72  2017-01-10 22:02:00+00:00              38000180     300.0   
73  2017-01-11 10:07:00+00:00              38000180    1000.0   
74  2017-01-11 04:33:00+00:00              38000180    1000.0   
75  2017-01-28 05:21:00+00:00              38000180    1000.0   
76  2017-01-29 22:55:00+00:00              38000180    1000.0   

                                    drug_source_value route_source_value  \
0                       CEFTRIAXON 100 MG/ML INJECTIE        intraveneus   
1                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
2                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
3                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
4                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
..                                                ...                ...   
72  VANCOMYCINE INFUUS >250 MG EN <=500 MG IN NACL...        intraveneus   
73         MEROPENEM KORTLOPEND INFUUS IN NACL (VUMC)        intraveneus   
74  VANCOMYCINE INFUUS >500 MG EN <=1250 MG IN NAC...        intraveneus   
75  VANCOMYCINE INFUUS >500 MG EN <=1250 MG IN NAC...        intraveneus   
76  VANCOMYCINE INFUUS >500 MG EN <=1250 MG IN NAC...        intraveneus   

   dose_unit_source_value  
0                      mg  
1                      mg  
2                      mg  
3                      mg  
4                      mg  
..                    ...  
72                     mg  
73                     mg  
74                     mg  
75                     mg  
76                     mg  

[77 rows x 11 columns]

Blood labs are in measurements as well.

In [ ]:
%%bigquery test --project esicmdatathon2026
select *
FROM measurement m
  WHERE
    measurement_concept_id in (3018405, 3047181, 3028271, 3005949, 3008037) -- searching for lactate
   and m.person_id = 56647 -- testing purpose, random visit
  limit 100


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test


person_id  measurement_concept_id measurement_date  \
0       56647                 3008037       2017-02-10   
1       56647                 3008037       2017-02-15   
2       56647                 3008037       2017-02-16   
3       56647                 3008037       2017-01-07   
4       56647                 3008037       2016-12-31   
..        ...                     ...              ...   
95      56647                 3018405       2017-01-11   
96      56647                 3018405       2017-01-12   
97      56647                 3018405       2017-01-12   
98      56647                 3018405       2017-01-12   
99      56647                 3018405       2017-01-12   

        measurement_datetime  measurement_type_concept_id  value_as_number  \
0  2017-02-10 23:00:00+00:00                            0              1.1   
1  2017-02-15 23:00:00+00:00                            0              1.5   
2  2017-02-16 23:00:00+00:00                            0              1.9   
3  2017-01-07 06:46:00+00:00                            0              1.6   
4  2016-12-31 11:49:00+00:00                            0              2.1   
..                       ...                          ...              ...   
95 2017-01-11 02:32:00+00:00                            0              2.2   
96 2017-01-12 14:13:00+00:00                            0              1.1   
97 2017-01-12 07:18:00+00:00                            0              1.1   
98 2017-01-12 19:08:00+00:00                            0              1.2   
99 2017-01-12 04:01:00+00:00                            0              1.2   

                            measurement_source_value unit_source_value  \
0      BLOEDGAS VOLLEDIG IC PAKKET;LACTAAT VEN. VUMC            mmol/L   
1      BLOEDGAS VOLLEDIG IC PAKKET;LACTAAT VEN. VUMC            mmol/L   
2      BLOEDGAS VOLLEDIG IC PAKKET;LACTAAT VEN. VUMC            mmol/L   
3   LACTAAT (BLOEDGAS);LACTAAT - BLOEDGAS VEN. (AMC)            mmol/L   
4   LACTAAT (BLOEDGAS);LACTAAT - BLOEDGAS VEN. (AMC)            mmol/L   
..                                               ...               ...   
95                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
96                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
97                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
98                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
99                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   

   value_source_value  
0                 1.1  
1                 1.5  
2                 1.9  
3                 1.6  
4                 2.1  
..                ...  
95                2.2  
96                1.1  
97                1.1  
98                1.2  
99                1.2  

[100 rows x 9 columns]

Visits do not have admission from and discharged to

In [ ]:
%%bigquery test --project esicmdatathon2026
select *
FROM visit_occurrence m
where person_id = 56647 -- testing purpose, random visit
  -- and admitted_from_source_value is not null
  limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test

visit_occurrence_id  person_id  visit_concept_id visit_start_date  \
0                25373      56647              9201       2017-01-01   
1                12474      56647              9201       2017-01-07   
2                72438      56647              9201       2017-01-10   
3                45162      56647              9201       2017-02-11   

       visit_start_datetime visit_end_date        visit_end_datetime  \
0 2017-01-01 00:00:00+00:00     2017-01-07 2017-01-07 01:26:00+00:00   
1 2017-01-07 11:19:00+00:00     2017-01-10 2017-01-10 06:07:00+00:00   
2 2017-01-10 06:53:00+00:00     2017-02-10 2017-02-10 05:15:00+00:00   
3 2017-02-11 03:45:00+00:00     2017-02-15 2017-02-15 04:34:00+00:00   

   visit_type_concept_id visit_source_value  admitted_from_concept_id  \
0                  32827                icu                         0   
1                  32827                icu                         0   
2                  32827                icu                         0   
3                  32827                icu                         0   

   discharged_to_concept_id admitted_from_source_value  \
0                         0                       None   
1                         0                       None   
2                         0                       None   
3                         0                       None   

  discharged_to_source_value  
0                       None  
1                       None  
2                       None  
3                       None

A person can have multiple visits. The tracheostomy was first found in the second visit in this example.

In [ ]:
%%bigquery test --project esicmdatathon2026
select d.person_id, visit_start_datetime, visit_end_datetime, min(measurement_datetime) as insert_trach
, timestamp_diff( min(measurement_datetime), min(visit_start_datetime),  hour)/24.0 as days_admit_to_first_trach
  from measurement d
inner join visit_occurrence v on d.person_id = v.person_id
       --   and timestamp_diff(v.visit_end_datetime, v.visit_start_datetime, hour )/24.0 >= 2 -- filter for longer patients only
where d.measurement_concept_id in ( 36305611  -- Tracheostomy tube diameter
        )
  and d.person_id = 56647
group by d.person_id, visit_start_datetime, visit_end_datetime


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test

person_id      visit_start_datetime        visit_end_datetime  \
0      56647 2017-01-01 00:00:00+00:00 2017-01-07 01:26:00+00:00   
1      56647 2017-01-07 11:19:00+00:00 2017-01-10 06:07:00+00:00   
2      56647 2017-01-10 06:53:00+00:00 2017-02-10 05:15:00+00:00   
3      56647 2017-02-11 03:45:00+00:00 2017-02-15 04:34:00+00:00   

               insert_trach  days_admit_to_first_trach  
0 2017-01-09 13:34:00+00:00                   8.541667  
1 2017-01-09 13:34:00+00:00                   2.083333  
2 2017-01-09 13:34:00+00:00                  -0.708333  
3 2017-01-09 13:34:00+00:00                 -32.583333

PEEP, FiO2 * co. testing existence of values and frequency of charting.


In [ ]:
%%bigquery test_exist_value --project esicmdatathon2026
select measurement_concept_id, c.concept_name, measurement_source_value
, count(*) as number_entries
, count(distinct person_id) as number_patients
, count(distinct cast(person_id as STRING) || cast(measurement_date as STRING)) as number_patient_days
from measurement m inner join concept c on m.measurement_concept_id = c.concept_id
where measurement_concept_id in (
  36305682 -- Bias flow setting Ventilator
  , 3043148 -- Breath rate mechanical --on ventilator
  , 3007469 -- Breath rate setting Ventilator
  , 1175625 -- Breath rate spontaneous
  , 3026892 -- Breath rate spontaneous --on ventilator
  , 40760768 -- Flow trigger setting Ventilator
  , 36305890 -- Inflation trigger pressure setting Ventilator
  , 3009065 -- Inspiration/Expiration setting Ventilator
  , 36304672 -- Inspiratory time setting Ventilator
  , 2000000220 -- Inspiratory time setting Ventilator perc
  , 3045410 -- Minute volume setting Ventilator
  , 3025408 -- Oxygen/Inspired gas Respiratory system by O2 Analyzer --on ventilator
  , 3011557 -- Peak inspiratory gas flow setting Ventilator
  , 3022875 -- Positive end expiratory pressure setting Ventilator
  , 3000461 -- Pressure support setting Ventilator
  , 36306157 -- Pressure.max Respiratory system airway --on ventilator
  , 21490854 -- Tidal volume Ventilator --on ventilator
  , 3012410 -- Tidal volume setting Ventilator
  , 3017594 -- Tidal volume.spontaneous --on ventilator
  , 3017878 -- Tidal volume.spontaneous+mechanical/Body weight [Volume/mass] --on ventilator
  , 21490879 -- Ventilator airway circuit leakage volume
  , 2000000634 -- non-invasive ventilator - leakage fraction
)
--  and person_id = 51316 -- testing purpose only
group by measurement_concept_id, measurement_source_value, concept_name
order by COUNT(*) desc

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test_exist_value


measurement_concept_id                                       concept_name  \
0                  3012410                    Tidal volume setting Ventilator   
1                  3022875  Positive end expiratory pressure setting Venti...   
2                 36304672                Inspiratory time setting Ventilator   
3                 36306157  Pressure.max Respiratory system airway --on ve...   
4                  3022875  Positive end expiratory pressure setting Venti...   
..                     ...                                                ...   
74                 3000461                Pressure support setting Ventilator   
75                40760768                    Flow trigger setting Ventilator   
76                36305682                       Bias flow setting Ventilator   
77                 3007469                     Breath rate setting Ventilator   
78                 3026892            Breath rate spontaneous --on ventilator   

                             measurement_source_value  number_entries  \
0                                TV;R UMCA AN VENT TV         5772125   
1                       PEEP/CPAP;R UMCA AN VENT PEEP         5735794   
2         Insp tijd ;R UMCA AN VENT INSPIRATIE TIJD S         4113839   
3                                P max;R UMCA AN PMAX         3785274   
4      PEEP/CPAP ;R UMCA ICU VENTILATOR PEEP/CPAP SET         2276558   
..                                                ...             ...   
74                          Pcontrol (ingesteld)HA/MA              19   
75                      Triggergevoeligheid (Set) (2)              10   
76                                      HFO-Bias-flow               3   
77     Frequentie ;R UMCA FREQUENTIE CPAP ONGEKOPPELD               3   
78  Adem frequentie Beademing Spontaan + beade(gem...               1   

    number_patients  number_patient_days  
0             17058                31216  
1             16471                29567  
2             14351                25746  
3             11931                21794  
4             19621                81973  
..              ...                  ...  
74               18                   19  
75                9                   10  
76                1                    1  
77                1                    1  
78                1                    1  

[79 rows x 6 columns]

In [ ]:
%%bigquery test_one_example --project esicmdatathon2026
select measurement_date, measurement_concept_id, concept_name, measurement_source_value, count(value_as_number)
from measurement m inner join concept c on m.measurement_concept_id = c.concept_id
where c.concept_name like '%Breath rate%'
and person_id = 51316 -- testing purpose only, random
group by  measurement_date, measurement_concept_id, concept_name, measurement_source_value
order by measurement_date

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test_one_example

# why does one day have both spontaneous and venatilator breathing?
# why is there no entry on 2017-01-04?

measurement_date  measurement_concept_id                    concept_name  \
0        2017-01-01                 1175625         Breath rate spontaneous   
1        2017-01-01                 3007469  Breath rate setting Ventilator   
2        2017-01-01                 3007469  Breath rate setting Ventilator   
3        2017-01-02                 3007469  Breath rate setting Ventilator   
4        2017-01-02                 1175625         Breath rate spontaneous   
5        2017-01-03                 1175625         Breath rate spontaneous   
6        2017-01-03                 3007469  Breath rate setting Ventilator   
7        2017-01-05                 1175625         Breath rate spontaneous   
8        2017-01-05                 3007469  Breath rate setting Ventilator   
9        2017-01-05                 3007469  Breath rate setting Ventilator   
10       2017-01-06                 1175625         Breath rate spontaneous   
11       2017-01-06                 3007469  Breath rate setting Ventilator   
12       2017-01-07                 1175625         Breath rate spontaneous   
13       2017-01-07                 3007469  Breath rate setting Ventilator   
14       2017-01-08                 1175625         Breath rate spontaneous   
15       2017-01-08                 3007469  Breath rate setting Ventilator   
16       2017-01-11                 3007469  Breath rate setting Ventilator   
17       2017-01-11                 1175625         Breath rate spontaneous   
18       2017-01-11                 3007469  Breath rate setting Ventilator   
19       2017-01-12                 1175625         Breath rate spontaneous   
20       2017-01-12                 3007469  Breath rate setting Ventilator   
21       2017-01-13                 1175625         Breath rate spontaneous   
22       2017-01-13                 3007469  Breath rate setting Ventilator   
23       2017-01-13                 3007469  Breath rate setting Ventilator   
24       2017-06-24                 3007469  Breath rate setting Ventilator   

                             measurement_source_value  f0_  
0   AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   22  
1   AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   22  
2   Ademfrequentie ;R UMCA ICU VENTILATOR RESP RATE S    2  
3   AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   24  
4   AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   24  
5   AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   18  
6   AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   18  
7   AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...    6  
8   AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...    5  
9   Ademfrequentie ;R UMCA ICU VENTILATOR RESP RATE S    3  
10  AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   23  
11  AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   23  
12  AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   24  
13  AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   24  
14  AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   10  
15  AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   10  
16  Ademfrequentie ;R UMCA ICU VENTILATOR RESP RATE S    3  
17  AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...    5  
18  AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...    5  
19  AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   24  
20  AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   24  
21  AF spont ;R UMCA ICU VENTILATOR RESPIRATORY RA...   17  
22  AF totaal;R UMCA ICU VENTILATOR RESPIRATORY RA...   17  
23  Ademfrequentie ;R UMCA ICU VENTILATOR RESP RATE S    3  
24  Ademfrequentie ;R UMCA ICU VENTILATOR RESP RATE S  231

In [ ]:
%%bigquery test_one_example --project esicmdatathon2026
select measurement_date, measurement_source_value, c.concept_name, measurement_concept_id, count(value_as_number)
from measurement m
inner join concept c
on m.measurement_concept_id = c.concept_id
where person_id = 51316 -- testing purpose only, random
  and measurement_date = '2017-01-04'
group by measurement_concept_id, measurement_source_value, c.concept_name, measurement_date
order by count(value_as_number) desc
limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test_one_example

measurement_date                         measurement_source_value  \
0        2017-01-04                        intake - Infuus medicatie   
1        2017-01-04                                  intake - Infuus   
2        2017-01-04  T kern (Celsius);R UMCA ICU KERN TEMP (CELSIUS)   
3        2017-01-04                           ST II;R UMCA ICU ST II   
4        2017-01-04                                     HF;R UMCA HF   
..              ...                                              ...   
60       2017-01-04                                  output - Faeces   
61       2017-01-04                        KREATININE;KREATININE AMC   
62       2017-01-04                                  GLUCOSE;GLUCOSE   
63       2017-01-04                                    KALIUM;KALIUM   
64       2017-01-04                                  NATRIUM;NATRIUM   

                                    concept_name  measurement_concept_id  f0_  
0            Fluid intake intravascular Measured                 3037253   52  
1            Fluid intake intravascular Measured                 3037253   38  
2                               Body temperature                 3020891   24  
3                                   ST deviation                 3017453   24  
4                 Heart rate.beat-to-beat by EKG                21490872   24  
..                                           ...                     ...  ...  
60                         Output.stool [Volume]                 3011087    1  
61  Creatinine [Moles/volume] in Serum or Plasma                 3020564    1  
62               Glucose [Moles/volume] in Blood                 3020491    1  
63             Potassium [Moles/volume] in Blood                 3005456    1  
64                Sodium [Moles/volume] in Blood                 3000285    1  

[65 rows x 5 columns]

In [ ]:
%%bigquery test --project esicmdatathon2026
select c.concept_name, m.*
from measurement m
inner join concept c
on m.measurement_concept_id = c.concept_id
where person_id = 51316 -- testing purpose only, random
  and measurement_concept_id = 42868484
  and measurement_date = '2017-01-04'
limit 100


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test

concept_name  person_id  \
0   Type of Positive airway pressure device      51316   
1   Type of Positive airway pressure device      51316   
2   Type of Positive airway pressure device      51316   
3   Type of Positive airway pressure device      51316   
4   Type of Positive airway pressure device      51316   
5   Type of Positive airway pressure device      51316   
6   Type of Positive airway pressure device      51316   
7   Type of Positive airway pressure device      51316   
8   Type of Positive airway pressure device      51316   
9   Type of Positive airway pressure device      51316   
10  Type of Positive airway pressure device      51316   
11  Type of Positive airway pressure device      51316   
12  Type of Positive airway pressure device      51316   
13  Type of Positive airway pressure device      51316   
14  Type of Positive airway pressure device      51316   
15  Type of Positive airway pressure device      51316   
16  Type of Positive airway pressure device      51316   
17  Type of Positive airway pressure device      51316   
18  Type of Positive airway pressure device      51316   
19  Type of Positive airway pressure device      51316   
20  Type of Positive airway pressure device      51316   
21  Type of Positive airway pressure device      51316   
22  Type of Positive airway pressure device      51316   

    measurement_concept_id measurement_date      measurement_datetime  \
0                 42868484       2017-01-04 2017-01-04 05:07:00+00:00   
1                 42868484       2017-01-04 2017-01-04 08:41:00+00:00   
2                 42868484       2017-01-04 2017-01-04 09:07:00+00:00   
3                 42868484       2017-01-04 2017-01-04 09:30:00+00:00   
4                 42868484       2017-01-04 2017-01-04 10:07:00+00:00   
5                 42868484       2017-01-04 2017-01-04 11:07:00+00:00   
6                 42868484       2017-01-04 2017-01-04 12:07:00+00:00   
7                 42868484       2017-01-04 2017-01-04 13:07:00+00:00   
8                 42868484       2017-01-04 2017-01-04 14:07:00+00:00   
9                 42868484       2017-01-04 2017-01-04 15:07:00+00:00   
10                42868484       2017-01-04 2017-01-04 16:07:00+00:00   
11                42868484       2017-01-04 2017-01-04 17:07:00+00:00   
12                42868484       2017-01-04 2017-01-04 19:07:00+00:00   
13                42868484       2017-01-04 2017-01-04 20:07:00+00:00   
14                42868484       2017-01-04 2017-01-04 21:07:00+00:00   
15                42868484       2017-01-04 2017-01-04 22:07:00+00:00   
16                42868484       2017-01-04 2017-01-04 23:07:00+00:00   
17                42868484       2017-01-04 2017-01-04 01:07:00+00:00   
18                42868484       2017-01-04 2017-01-04 02:07:00+00:00   
19                42868484       2017-01-04 2017-01-04 04:07:00+00:00   
20                42868484       2017-01-04 2017-01-04 06:07:00+00:00   
21                42868484       2017-01-04 2017-01-04 07:07:00+00:00   
22                42868484       2017-01-04 2017-01-04 08:07:00+00:00   

    measurement_type_concept_id  value_as_number  \
0                             0             10.0   
1                             0             10.0   
2                             0             10.0   
3                             0             10.0   
4                             0             10.0   
5                             0             10.0   
6                             0             10.0   
7                             0             10.0   
8                             0             10.0   
9                             0             10.0   
10                            0             10.0   
11                            0             10.0   
12                            0             10.0   
13                            0             10.0   
14                            0             10.0   
15                            0             10.0   
1

In [15]:
%%bigquery test --project esicmdatathon2026
select distinct measurement_source_value, measurement_concept_id, concept_name
, count(*) as entries, count(distinct person_id) as persons
, min(value_as_number) as min_value, max(value_as_number) as max_value
, avg(value_as_number) as avg_value
from measurement m
inner join concept c
on m.measurement_concept_id = c.concept_id
where measurement_concept_id = 3024928
group by measurement_source_value, measurement_concept_id, concept_name


Query is running:   0%|          |

Downloading:   0%|          |

In [16]:
test

measurement_source_value  measurement_concept_id  \
0            BLOEDGAS VOLLEDIG;SO2 VEN. VUMC                 3024928   
1        POCT BLOED - BLOEDGAS;SO2 VEN. VUMC                 3024928   
2                          SO2;SO2 VEN. VUMC                 3024928   
3                S02 Ven;R UMCA PERF SO2 VEN                 3024928   
4                        SV02;R UMCA AN SVO2                 3024928   
5  BLOEDGAS VOLLEDIG IC PAKKET;SO2 VEN. VUMC                 3024928   
6                  AFNAME POCT;SO2 VEN. VUMC                 3024928   

                        concept_name  entries  persons  min_value  max_value  \
0  Oxygen saturation in Venous blood      925      560       0.09       0.99   
1  Oxygen saturation in Venous blood     8772     2667       0.06       1.00   
2  Oxygen saturation in Venous blood     9570     2996       0.07       1.00   
3  Oxygen saturation in Venous blood   278280     1722      35.00     100.00   
4  Oxygen saturation in Venous blood    13113      301       0.00     100.00   
5  Oxygen saturation in Venous blood      855      492       0.15       0.99   
6  Oxygen saturation in Venous blood        1        1       0.85       0.85   

   avg_value  
0   0.807535  
1   0.703087  
2   0.700936  
3  80.103766  
4  78.767490  
5   0.783754  
6   0.850000

In [ ]:
%%bigquery test --project esicmdatathon2026
select *
from observation
where observation_concept_id in (3042082 --Confusion Assessment Method (CAM)
)
limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test

person_id  observation_concept_id observation_date  \
0       13316                 3042082       2006-08-07   
1       13316                 3042082       2006-08-07   
2       13316                 3042082       2006-08-07   
3       13316                 3042082       2006-08-07   
4       57364                 3042082       2006-12-10   
..        ...                     ...              ...   
95      14704                 3042082       2007-01-04   
96      14704                 3042082       2007-01-04   
97      14704                 3042082       2007-01-04   
98      14704                 3042082       2007-01-04   
99      14704                 3042082       2007-01-05   

        observation_datetime  observation_type_concept_id  value_as_number  \
0  2006-08-07 04:33:00+00:00                            0              0.0   
1  2006-08-07 04:33:00+00:00                            0              0.0   
2  2006-08-07 16:33:00+00:00                            0              0.0   
3  2006-08-07 16:33:00+00:00                            0              0.0   
4  2006-12-10 05:51:00+00:00                            0              0.0   
..                       ...                          ...              ...   
95 2007-01-04 04:27:00+00:00                            0              0.0   
96 2007-01-04 16:27:00+00:00                            0              0.0   
97 2007-01-04 16:27:00+00:00                            0              0.0   
98 2007-01-04 16:27:00+00:00                            0              0.0   
99 2007-01-05 04:27:00+00:00                            0              0.0   

      observation_source_value unit_source_value value_source_value  
0   CAM-ICU fluctuerend beloop                                  0.0  
1   CAM-ICU fluctuerend beloop                                  0.0  
2   CAM-ICU fluctuerend beloop                                  0.0  
3   CAM-ICU fluctuerend beloop                                  0.0  
4   CAM-ICU fluctuerend beloop                                  0.0  
..                         ...               ...                ...  
95  CAM-ICU fluctuerend beloop                                  0.0  
96  CAM-ICU fluctuerend beloop                                  0.0  
97  CAM-ICU fluctuerend beloop                                  0.0  
98  CAM-ICU fluctuerend beloop                                  0.0  
99  CAM-ICU fluctuerend beloop                                  0.0  

[100 rows x 9 columns]

# Heart rate
I want to try something with HRV

In [ ]:
%%bigquery test --project esicmdatathon2026
select c.concept_name, m.measurement_source_value
, max(measurement_date) as last_date_used
, count(distinct person_id) as person_count
, count(*) as number_of_entries
from measurement m
inner join concept c
on m.measurement_concept_id = c.concept_id
where measurement_concept_id in (
  3027018 -- Heart rate
	, 21490670 --Heart rate Intra arterial line by Invasive
	, 3003841 --Heart rate Peripheral artery by palpation
	, 3001376 --Heart rate by Pulse oximetry
	, 3022318 --Heart rate rhythm
	, 3044421 --Heart rate rhythm palpation
	, 21490872 --Heart rate.beat-to-beat by EKG
)
group by concept_name, measurement_source_value
order by count(*) desc


Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
test


concept_name  \
0               Heart rate.beat-to-beat by EKG   
1                 Heart rate by Pulse oximetry   
2    Heart rate Peripheral artery by palpation   
3                                   Heart rate   
4                 Heart rate by Pulse oximetry   
5                 Heart rate by Pulse oximetry   
6                 Heart rate by Pulse oximetry   
7                                   Heart rate   
8   Heart rate Intra arterial line by Invasive   
9                            Heart rate rhythm   
10                 Heart rate rhythm palpation   
11                                  Heart rate   
12                                  Heart rate   
13                           Heart rate rhythm   
14                                  Heart rate   
15                                  Heart rate   
16                Heart rate by Pulse oximetry   
17                                  Heart rate   
18                                  Heart rate   

                          measurement_source_value last_date_used  \
0                                     HF;R UMCA HF     2023-11-27   
1              HF monitor;R UMCA AN HARTFREQUENTIE     2023-10-16   
2                              Pols;R UMCA AN POLS     2023-10-16   
3                                   Hartfrequentie     2015-09-16   
4       HF (monitor);R UMCA HARTFREQUENTIE MONITOR     2023-11-27   
5                   Pols (monitor);R UMCA ICU POLS     2022-06-16   
6                          Polsfrequentie;POLSSLAG     2023-12-03   
7                            Pulse;R CV XPER PULSE     2023-08-16   
8                          PiCCO HF Hartfrequentie     2005-09-23   
9                       Hartritme;R UMCA HARTRITME     2023-05-19   
10                 Regelmaat;R UMCA REGELMAAT POLS     2023-01-22   
11                 Heart Rate;R CV XPER HEART RATE     2023-08-16   
12                       Pols;R UMCA MYCHART PULSE     2023-02-25   
13           Ritme monitor;R UMCA AN RITME MONITOR     2022-07-30   
14           hartfrequentie;R UMCA CARD FREQUENTIE     2018-03-13   
15             HF rust;R UMCA REV KARVONEN HF RUST     2019-02-15   
16                    Polsslag;ANESTHESIE POLSSLAG     2016-08-29   
17  Hartslag linker arm;R UMCA EAI HARTSLAG RECHTS     2016-12-31   
18   Hartslag linker arm;R UMCA EAI HARTSLAG LINKS     2016-12-31   

    person_count  number_of_entries  
0          25154            9614876  
1          18407            6407923  
2          17459            5561559  
3          40101            4531237  
4          25112            3207340  
5          21568            2774726  
6          22909            1691850  
7           1152              31465  
8             45               4330  
9           1724               2390  
10          1663               1946  
11           610               1712  
12            22                957  
13             7                174  
14           121                143  
15           118                137  
16             1                 20  
17             1                  1  
18             1                  1

In [ ]:
%%bigquery test --project esicmdatathon2026
select person_id, measurement_date, stddev_samp(value_as_number) as sd
from measurement m
inner join concept c
on m.measurement_concept_id = c.concept_id
where measurement_concept_id in ( 21490872 --Heart rate.beat-to-beat by EKG
) and value_as_number > 0 and value_as_number < 300
group by person_id, measurement_date

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
import plotly.express as px

df = test
fig = px.histogram(df['sd'], x="sd")
fig.show()
